In [66]:
import ast
import json
import requests
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.ticker import StrMethodFormatter
from matplotlib.dates import DateFormatter
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Activation, Dense, Dropout, LSTM
from sklearn import metrics 
# USDC: baseCurrency:  "0xa0b86991c6218b36c1d19d4a2e9eb0ce3606eb48"
# quoteCurrency:  "0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2"

# A simple function to use requests.post to make the API call.

def query_uniswap_subgraph(pool_address, page_size=100, start_timestamp=1630489200):
    uniswap_subgraph_url = "https://api.thegraph.com/subgraphs/name/uniswap/uniswap-v3"

    # Initialize an empty DataFrame to store all the results
    df_all = pd.DataFrame()

    # Set the initial value for skip
    skip = 0

    while True:
        graphql_query = """
        {
          pool(id: "%s") {
            id
            createdAtTimestamp
            token0 {
              symbol
              name
              decimals
            }
            token1 {
              symbol
              name
              decimals
            }
            tick
            feeTier
            liquidity
            volumeUSD
            token0Price
            token1Price
            swaps(first: %d, skip: %d, orderBy: timestamp, orderDirection: desc, where: { timestamp_gt: %d }) {
              id
              timestamp
              amount0
              amount1
              amountUSD
            }
          }
        }
        """ % (pool_address, page_size, skip, start_timestamp)

        response = requests.post(uniswap_subgraph_url, json={"query": graphql_query})

        if response.status_code == 200:
            data = response.json()
            
            # Fetch pool data
            pool_data = data.get("data", {}).get("pool", {})
            
            # Check if there are no more results
            swaps_data = pool_data.get("swaps", [])
            if not swaps_data:
                break

            # Convert to DataFrame and append to the overall DataFrame
            df_pool = pd.DataFrame([pool_data] * len(swaps_data))
            df_swaps = pd.json_normalize(swaps_data)
            
            # Combine pool and swaps data using a common index
            df = pd.concat([df_pool, df_swaps], axis=1)
            df_all = pd.concat([df_all, df], ignore_index=True)

            # Increment skip for the next iteration
            skip += page_size

        else:
            print(f"Error: {response.status_code}")
            return None
          
    df_all["USDC Symbol"] = df_all["token0"].apply(lambda x: x["symbol"])
    df_all["USDC Name"] = df_all["token0"].apply(lambda x: x["name"])
    df_all["USDC Decimal"] = df_all["token0"].apply(lambda x: x["decimals"])
    df_all["WETH Symbol"] = df_all["token1"].apply(lambda x: x["symbol"])
    df_all["WETH Name"] = df_all["token1"].apply(lambda x: x["name"])
    df_all["WETH Decimal"] = df_all["token1"].apply(lambda x: x["decimals"])
    
    df_all = df_all.iloc[:, 1:]

    column_mapping = {
    'amount0': 'USDC Amount',
    'amount1': 'WETH Amount',
    'amountUSD': 'USD Amount',
    'token0Price': 'USDC Price',
    'token1Price': 'WETH Price',
    'feeTier': 'Fee Tier',
    'id': 'Swap ID',
    
    # Add more mappings as needed
  }

  # Rename the columns
    df_all.rename(columns=column_mapping, inplace=True)
    
    

    return df_all[['Swap ID', 'tick', 'Fee Tier',
       'liquidity', 'volumeUSD', 'USDC Price', 'WETH Price', 'swaps',
       'timestamp', 'USDC Amount', 'WETH Amount', 'USD Amount']]

# Replace with the actual Uniswap pool address
pool_address = "0x88e6a0c2ddd26feeb64f039a2c41296fcb3f5640" 

# Query the Uniswap subgraph for historical data with pagination
result = query_uniswap_subgraph(pool_address, page_size=100)

# Print the resulting DataFrame
print(result)
# Print the DataFrame

                                                Swap ID    tick Fee Tier  \
0     0x961cee4e468dba05a3e48b74e2975df621608a434587...  198487      500   
1     0x77a757b543b86a48c33a434a68754ca5db9cbec3efc2...  198487      500   
2     0xeb2ca529909db369bf03d3c9020260980e6abd4fcba5...  198487      500   
3     0x9d7c0b9cdb94d3c85d291e7c12ded960ee086f56fc39...  198487      500   
4     0x254fb671daae981bbf5252ab5d24bcc1df36194fc1b4...  198487      500   
...                                                 ...     ...      ...   
5095  0x20c4fd43394f65cb82137f88722ed879a2ef4dd4e30f...  198492      500   
5096  0x26d658b9158b862be993dc6eb2a490a5047cb254bbf5...  198492      500   
5097  0xc318f785987c3eec057c494908a4ef482c2dc58c760b...  198492      500   
5098  0x6c74469febc0fb26779a10ad937585bd98b907d83351...  198492      500   
5099  0x4208f4153361be3cd308802516e2167d45dd1ac0e24c...  198492      500   

                 liquidity                            volumeUSD  \
0      8043457483253

In [16]:
import ast
import json
import requests
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.ticker import StrMethodFormatter
from matplotlib.dates import DateFormatter
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Activation, Dense, Dropout, LSTM
from sklearn import metrics 

def fetch_historical_data(pool_address, start_timestamp, end_timestamp, page_size):
    df_all = pd.DataFrame()
    pool_cursor = None
    swaps_cursor = None
    uniswap_subgraph_url = "https://api.thegraph.com/subgraphs/name/uniswap/uniswap-v3"

    while True:
        print(f"Fetching data from Pool: {pool_cursor or start_timestamp}, Swaps: {swaps_cursor or start_timestamp}...")
        
        graphql_query = """
        {
          pools(
            first: %d
            orderBy: createdAtTimestamp
            orderDirection: asc
            where: { createdAtTimestamp_gt: %d }
            after: "%s"
          ) {
            id
            createdAtTimestamp
            token0 {
              symbol
              name
              decimals
            }
            token1 {
              symbol
              name
              decimals
            }
            tick
            feeTier
            liquidity
            volumeUSD
            token0Price
            token1Price
            swaps(
              first: %d
              orderBy: timestamp
              orderDirection: desc
              where: { timestamp_gt: %d }
              after: "%s"
            ) {
              id
              timestamp
              amount0
              amount1
              amountUSD
            }
          }
        }
        """ % (page_size, start_timestamp, pool_cursor or "", page_size, start_timestamp, swaps_cursor or "")

        response = requests.post(uniswap_subgraph_url, json={"query": graphql_query})

        if response.status_code == 200:
            data = response.json()
            pools_data = data.get("data", {}).get("pools", [])
            
            if not pools_data:
                # If no more pools data, break the loop
                break

            pool_data = pools_data[0]
            swaps_data = pool_data.get("swaps", [])

            # Update the cursors for the next iteration
            pool_cursor = pool_data.get("createdAtTimestamp", "")
            swaps_cursor = None if not swaps_data or swaps_data[-1]['timestamp'] == swaps_cursor else swaps_data[-1]['timestamp']

            df_pool = pd.DataFrame([pool_data] * len(swaps_data))
            df_swaps = pd.json_normalize(swaps_data)
            df = pd.concat([df_pool, df_swaps], axis=1)
            df_all = pd.concat([df_all, df], ignore_index=True)

        else:
            print(f"Error: {response.status_code}")
            return None

    return df_all

# Replace with the actual Uniswap pool address
pool_address = "0x88e6a0c2ddd26feeb64f039a2c41296fcb3f5640"

# Example usage
data = fetch_historical_data(pool_address, 1630489200, 1670643600, 100)

# Replace with the actual Uniswap pool address
pool_address = "0x88e6a0c2ddd26feeb64f039a2c41296fcb3f5640" 

# Example usage
data = fetch_historical_data(pool_address, 1630489200, 1670643600, 100)

Fetching data from Pool: 1630489200, Swaps: 1630489200...
Fetching data from Pool: 1630504095, Swaps: 1633221976...
Fetching data from Pool: 1630504095, Swaps: 1630489200...
Fetching data from Pool: 1630504095, Swaps: 1633221976...
Fetching data from Pool: 1630504095, Swaps: 1630489200...
Fetching data from Pool: 1630504095, Swaps: 1633221976...
Fetching data from Pool: 1630504095, Swaps: 1630489200...


KeyboardInterrupt: 

In [14]:
data

Empty DataFrame
Columns: []
Index: []

In [67]:
result

Swap ID    tick Fee Tier  \
0     0x961cee4e468dba05a3e48b74e2975df621608a434587...  198487      500   
1     0x77a757b543b86a48c33a434a68754ca5db9cbec3efc2...  198487      500   
2     0xeb2ca529909db369bf03d3c9020260980e6abd4fcba5...  198487      500   
3     0x9d7c0b9cdb94d3c85d291e7c12ded960ee086f56fc39...  198487      500   
4     0x254fb671daae981bbf5252ab5d24bcc1df36194fc1b4...  198487      500   
...                                                 ...     ...      ...   
5095  0x20c4fd43394f65cb82137f88722ed879a2ef4dd4e30f...  198492      500   
5096  0x26d658b9158b862be993dc6eb2a490a5047cb254bbf5...  198492      500   
5097  0xc318f785987c3eec057c494908a4ef482c2dc58c760b...  198492      500   
5098  0x6c74469febc0fb26779a10ad937585bd98b907d83351...  198492      500   
5099  0x4208f4153361be3cd308802516e2167d45dd1ac0e24c...  198492      500   

                 liquidity                            volumeUSD  \
0      8043457483253230877  416627398004.9623127004683021783558   
1      8043457483253230877  416627398004.9623127004683021783558   
2      8043457483253230877  416627398004.9623127004683021783558   
3      8043457483253230877  416627398004.9623127004683021783558   
4      8043457483253230877  416627398004.9623127004683021783558   
...                    ...                                  ...   
5095  17518107006508806805  416627550243.0705563399267771397254   
5096  17518107006508806805  416627550243.0705563399267771397254   
5097  17518107006508806805  416627550243.0705563399267771397254   
5098  17518107006508806805  416627550243.0705563399267771397254   
5099  17518107006508806805  416627550243.0705563399267771397254   

                               USDC Price  \
0     2400.189005775134059422293106522274   
1     2400.189005775134059422293106522274   
2     2400.189005775134059422293106522274   
3     2400.189005775134059422293106522274   
4     2400.189005775134059422293106522274   
...                                   ...   
5095  2398.961378948924461845728740600487   
5096  2398.961378948924461845728740600487   
5097  2398.961378948924461845728740600487   
5098  2398.961378948924461845728740600487   
5099  2398.961378948924461845728740600487   

                                   WETH Price  \
0     0.0004166338557479780256310722108001717   
1     0.0004166338557479780256310722108001717   
2     0.0004166338557479780256310722108001717   
3     0.0004166338557479780256310722108001717   
4     0.0004166338557479780256310722108001717   
...                                       ...   
5095  0.0004168470608885490890443005017725254   
5096  0.0004168470608885490890443005017725254   
5097  0.0004168470608885490890443005017725254   
5098  0.0004168470608885490890443005017725254   
5099  0.0004168470608885490890443005017725254   

                                                  swaps   timestamp  \
0     [{'id': '0x961cee4e468dba05a3e48b74e2975df6216...  1702110419   
1     [{'id': '0x961cee4e468dba05a3e48b74e2975df6216...  1702110419   
2     [{'id': '0x961cee4e468dba05a3e48b74e2975df6216...  1702110371   
3     [{'id': '0x961cee4e468dba05a3e48b74e2975df6216...  1702110371   
4     [{'id': '0x961cee4e468dba05a3e48b74e2975df6216...  1702110359   
...                                                 ...         ...   
5095  [{'id': '0x67462386f4063e9cdeb3aa080aa19575c70...  1702025951   
5096  [{'id': '0x67462386f4063e9cdeb3aa080aa19575c70...  1702025927   
5097  [{'id': '0x67462386f4063e9cdeb3aa080aa19575c70...  1702025903   
5098  [{'id': '0x67462386f4063e9cdeb3aa080aa19575c70...  1702025879   
5099  [{'id': '0x67462386f4063e9cdeb3aa080aa19575c70...  1702025855   

        USDC Amount              WETH Amount  \
0      -4118.453033     1.716727397824859011   
1      -3756.614133     1.565867930333992329   
2           7481.25    -3.115318161858165546   
3      33030.012035   -13.755665215960236177   
4      -1139.334402                    0.475   
...             ...                      ...   
5095   2608

In [69]:
result['swaps'][0]

[{'id': '0x961cee4e468dba05a3e48b74e2975df621608a4345876bd97cc244027c3e6a0e#5858179',
  'timestamp': '1702110419',
  'amount0': '-4118.453033',
  'amount1': '1.716727397824859011',
  'amountUSD': '4113.96308039909440998524591506064'},
 {'id': '0x77a757b543b86a48c33a434a68754ca5db9cbec3efc2e7b1eaf1347cbd8922de#5858178',
  'timestamp': '1702110419',
  'amount0': '-3756.614133',
  'amount1': '1.565867930333992329',
  'amountUSD': '3752.481204322258170282138653614799'},
 {'id': '0xeb2ca529909db369bf03d3c9020260980e6abd4fcba55e0619ea63ce8bbbc752#5858177',
  'timestamp': '1702110371',
  'amount0': '7481.25',
  'amount1': '-3.115318161858165546',
  'amountUSD': '7469.323070211574604242725087518155'},
 {'id': '0x9d7c0b9cdb94d3c85d291e7c12ded960ee086f56fc3989189e6da5ada831617b#5858176',
  'timestamp': '1702110371',
  'amount0': '33030.012035',
  'amount1': '-13.755665215960236177',
  'amountUSD': '32979.04586203212434231933952428921'},
 {'id': '0x254fb671daae981bbf5252ab5d24bcc1df36194fc1b48d6d

In [72]:
# Timestamp to datetime
result['timestamp'] = pd.to_datetime(result['timestamp'], unit='s')
result.sort_values(by='timestamp', inplace=True)

In [74]:
result.set_index('timestamp', inplace=True)

In [76]:
result.to_csv('data.csv')

In [1]:

import requests
import json

def fetch_all_swaps(graphql_endpoint, graphql_query):
    # Set up the request headers
    headers = {
        'Content-Type': 'application/json',
    }

    # Initialize variables
    all_swaps = []
    has_more = True
    skip = 0

    while has_more:
        # Set the current skip value in the GraphQL query
        query_with_skip = graphql_query.replace('skip: 0', f'skip: {skip}')
        print(f"Requesting data with skip: {skip}...")

        # Create a dictionary for the GraphQL request
        graphql_request = {
            'query': query_with_skip,
            'variables': {},
        }

        # Make the GraphQL request
        response = requests.post(graphql_endpoint, headers=headers, data=json.dumps(graphql_request))

        # Check if the request was successful (status code 200)
        if response.status_code == 200:
            # Parse the JSON response
            result = response.json()

            # Extract the data field from the result
            data = result.get('data')

            # Check if data is not empty and append to the list
            if data:
                swaps = data.get('swaps', [])
                all_swaps.extend(swaps)

                # Check if there are more results
                has_more = len(swaps) > 0
                skip += len(swaps)
            else:
                print("No data returned.")
                break
        else:
            print(f"GraphQL request failed with status code: {response.status_code}")
            print(response.text)
            break

    return all_swaps

graphql_endpoint = "https://api.thegraph.com/subgraphs/name/uniswap/uniswap-v3"
graphql_query = """
query {
  swaps(
    where: { pool_in: ["0x88e6a0c2ddd26feeb64f039a2c41296fcb3f5640"] }
    skip: 0
    first: 1000
    orderBy: timestamp
    orderDirection: asc
  ) {
    id
    transaction {
      id
    }
    timestamp
    pool {
      id
    }
    token0 {
      id
      symbol
    }
    token1 {
      id
      symbol
    }
    sender
    recipient
    origin
    amount0
    amount1
    amountUSD
    sqrtPriceX96
    tick
    logIndex
  }
}
"""

all_swaps = fetch_all_swaps(graphql_endpoint, graphql_query)

# Print or process all_swaps as needed
print(json.dumps(all_swaps, indent=2))
  



Requesting data with skip: 0...
Requesting data with skip: 1000...
Requesting data with skip: 2000...
Requesting data with skip: 3000...
Requesting data with skip: 4000...
Requesting data with skip: 5000...
Requesting data with skip: 6000...
No data returned.
[
  {
    "id": "0x0804ff007263a885191f23c808a9346e62d502a1fc23be82eb14052408d76ae2#2",
    "transaction": {
      "id": "0x0804ff007263a885191f23c808a9346e62d502a1fc23be82eb14052408d76ae2"
    },
    "timestamp": "1620252901",
    "pool": {
      "id": "0x88e6a0c2ddd26feeb64f039a2c41296fcb3f5640"
    },
    "token0": {
      "id": "0xa0b86991c6218b36c1d19d4a2e9eb0ce3606eb48",
      "symbol": "USDC"
    },
    "token1": {
      "id": "0xc02aaa39b223fe8d0a0e5c4f27ead9083c756cc2",
      "symbol": "WETH"
    },
    "sender": "0xe592427a0aece92de3edee1f18e0157c05861564",
    "recipient": "0xe592427a0aece92de3edee1f18e0157c05861564",
    "origin": "0x4a12b86c7c0270443760fe85c7d1e6bc62f78e4e",
    "amount0": "-119.744094",
    "amount1"

In [2]:
import pandas as pd

df = pd.json_normalize(all_swaps)

In [3]:
# Replace column names
new_df = df.rename(columns={
    'id': 'ID',
    'transaction.id': 'Transaction ID',
    'timestamp': 'Timestamp (Unix)',
    'pool.id': 'Pool ID',
    'sender': 'Sender',
    'recipient': 'Recipient',
    'origin': 'Origin',
    'token0.symbol': 'Token 0 Symbol',
    'token1.symbol': 'Token 1 Symbol',
    'token0.id': 'Token 0',
    'token1.id': 'Token 1',
    'amount0': 'Amount 0',
    'amount1': 'Amount 1',
    'amountUSD': 'Amount USD',
    'sqrtPriceX96': 'Sqrt Price X96',
    'tick': 'Tick',
    'logIndex': 'Log Index'
})
    
    

In [4]:
new_df['Timestamp'] = pd.to_datetime(new_df['Timestamp (Unix)'], unit='s')

In [5]:
new_df

ID Timestamp (Unix)  \
0     0x0804ff007263a885191f23c808a9346e62d502a1fc23...       1620252901   
1     0x53d4bc1240410e1c7907b8049f2355e226f5fcae8c16...       1620257875   
2     0x730978754a9a3db693148ac99b5d807555b2e7c1d664...       1620258696   
3     0x121c9e49d7a44eaa01e50070df2e4d8a95aace62ddfe...       1620258994   
4     0x26fd434e17ef8607ba00e09292232ebf45687c95603d...       1620259056   
...                                                 ...              ...   
5995  0x90929dbe8c12e0ee9c362ba9b15de79bc356dc5aef3b...       1620684055   
5996  0x06c15d4c81e381a85c4b4f6f92e52455c7f97a8f0041...       1620684060   
5997  0xb6058b799e8a84c84493ad1c4b6c4adaa3813a1cc283...       1620684365   
5998  0x00b0ceac48ca3a8881775ed3ee630e2df0fc46df453c...       1620684401   
5999  0x5cdff0a2009d0076f89aee17efe06d162f6fbfcfc432...       1620684401   

                                          Sender  \
0     0xe592427a0aece92de3edee1f18e0157c05861564   
1     0xe592427a0aece92de3edee1f18e0157c05861564   
2     0xe592427a0aece92de3edee1f18e0157c05861564   
3     0xe592427a0aece92de3edee1f18e0157c05861564   
4     0xe592427a0aece92de3edee1f18e0157c05861564   
...                                          ...   
5995  0xe592427a0aece92de3edee1f18e0157c05861564   
5996  0xe592427a0aece92de3edee1f18e0157c05861564   
5997  0xe592427a0aece92de3edee1f18e0157c05861564   
5998  0xe592427a0aece92de3edee1f18e0157c05861564   
5999  0xe592427a0aece92de3edee1f18e0157c05861564   

                                       Recipient  \
0     0xe592427a0aece92de3edee1f18e0157c05861564   
1     0xe592427a0aece92de3edee1f18e0157c05861564   
2     0xe592427a0aece92de3edee1f18e0157c05861564   
3     0xe592427a0aece92de3edee1f18e0157c05861564   
4     0xe592427a0aece92de3edee1f18e0157c05861564   
...                                          ...   
5995  0xe592427a0aece92de3edee1f18e0157c05861564   
5996  0xe592427a0aece92de3edee1f18e0157c05861564   
5997  0x990ba0d9bb24d7e89853bc61765a5a4f9b61a0d6   
5998  0xe592427a0aece92de3edee1f18e0157c05861564   
5999  0x0000000000007f150bd6f54c40a34d7c3d5e9f56   

                                          Origin       Amount 0  \
0     0x4a12b86c7c0270443760fe85c7d1e6bc62f78e4e    -119.744094   
1     0x60d46c943f13d605c1700d2944c035f4b5255ad2     499.756414   
2     0xc7bad783e498a5d9edcdf88ec011e1de89a54002            365   
3     0xbcf224cb3771bb32b7a9d49d573375ffa5e29b9d    -176.180828   
4     0xc6298e747259f11307750eeafdd8f3d3a6f312ed    -514.279985   
...                                          ...            ...   
5995  0xa68b40b05ec8da3b61ca4de3d1936a36c92eb8ab          10000   
5996  0x685ce7eeb6e8acb88e4bd5260bde646fd5f430b2   -2003.834813   
5997  0x990ba0d9bb24d7e89853bc61765a5a4f9b61a0d6  -11610.621171   
5998  0xcb5dd655ea0c6a07878433e756b2871dbdf45a64    18118.01049   
5999  0x0197abe48f0a9826d10f44dad7050f26586eb9ba         100000   

                    Amount 1                           Amount USD  \
0                      0.035  119.2881007156144668372176276273185   
1      -0.144241064315415179   508.178600761864081028446434489469   
2      -0.103492428467657963  368.6509112192267335333699915272717   
3                       0.05  177.6125155041179680250369011990548   
4                      0.146   518.543096308574289369562872032752   
...                      ...                                  ...   
5995   -2.494185083352995961   10103.6553826750584583635780938313   
5996                     0.5  2025.019781098570395079112901472941   
5997                     2.9  11787.98406913294643867158618133623   
5998   -4.450927255922106141  18241.31210988219519989096756393264   
5999  -24.788038679770686089  101126.9628048893946294203869987132   

                          Sqrt Price X96    Tick Log Index  \
0     1358206768703179146794161129278934  194996        73   
1     1334545912983135722438993170925379  194645       240   
2     1334315597745343730478188229716159  194641       133   
3     13

In [42]:
import requests
import json

def fetch_tick_day_datas(start_date_unix_timestamp=1684800000, tick_idx_gte=100, tick_idx_lte=200):
    graphql_endpoint = "https://api.thegraph.com/subgraphs/name/uniswap/uniswap-v3"
    
    
    pool_id = "0xcbcdf9626bc03e24f779434178a73a0b4bad62ed"
    
    graphql_query = f"""
    {{
      tickDayDatas(
        where: {{
          date_in: [{start_date_unix_timestamp}],
          pool_in: ["{pool_id}"],
        
        }},
        skip: 0,
        first: 1000,
        orderBy: date,
        orderDirection: asc
      ) {{
        id
        date
        pool {{
          id
          token0 {{
            id
            symbol
          }}
          token1 {{
            id
            symbol
          }}
        }}
        tick {{
          id
          tickIdx
        }}
        liquidityGross
        liquidityNet
        volumeToken0
        volumeToken1
        volumeUSD
        feesUSD
        feeGrowthOutside0X128
        feeGrowthOutside1X128
      }}
}}
    """
  
    headers = {
        'Content-Type': 'application/json',
    }

    data = {
        'query': graphql_query,
    }

    response = requests.post(graphql_endpoint, headers=headers, json=data)

    if response.status_code == 200 and response.json().get('data'):
        output = response.json()
        #print(output)
        df = pd.json_normalize(output['data']['tickDayDatas'])
        return df
    else:
        print(f"Error: {response.status_code}")
        print(response.text)  # Print the response content for debugging
        return None


tick_day_datas = fetch_tick_day_datas()

# Print or process tick_day_datas as needed
tick_day_datas

id        date  \
0   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#248...  1684800000   
1   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#250...  1684800000   
2   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#255...  1684800000   
3   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#255...  1684800000   
4   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#255...  1684800000   
5   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#255...  1684800000   
6   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#256...  1684800000   
7   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#256...  1684800000   
8   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#256...  1684800000   
9   0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#257...  1684800000   
10  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#257...  1684800000   
11  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#257...  1684800000   
12  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#257...  1684800000   
13  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#257...  1684800000   
14  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#258...  1684800000   
15  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#258...  1684800000   
16  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#258...  1684800000   
17  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#259...  1684800000   
18  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#259...  1684800000   
19  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#260...  1684800000   
20  0xcbcdf9626bc03e24f779434178a73a0b4bad62ed#264...  1684800000   

        liquidityGross         liquidityNet volumeToken0 volumeToken1  \
0      220229807112200      220229807112200            0            0   
1      211777871046918      211777871046918            0            0   
2     3562723699495342     3562723699495342            0            0   
3     3779855271516502     3779855271516502            0            0   
4     9241395024467951     9241395024467951            0            0   
5     3851643459857549     3851643459857549            0            0   
6    18071529805195302    15540431593282758            0            0   
7     6276981263978039     4160841542222451            0            0   
8    16109818336312841    15664494430758565            0            0   
9    67739321261280168    27048813621916528            0            0   
10   54257733022881155   -54228207325474005            0            0   
11   20662034027670638   -20195810710119926            0            0   
12   30084646196551104   -30031512198067246            0            0   
13   53052173862149327   -52756547412016017            0            0   
14  101748106355318710  -101648243390847912            0            0   
15    3017360332346402    -3017360332346402            0            0   
16    2056069383442604    -2056069383442604            0            0   
17  300478523129794760  -300478523129794760            0            0   
18  292830024502863001  -292830024502863001            0            0   
19   17711308983800199   -17711308983800199            0            0   
20     325762033354347     -325762033354347            0            0   

   volumeUSD feesUSD             feeGrowthOutside0X128  \
0          0       0     87384785569166117729186238833   
1          0       0  10938791505542220369696872818604   
2          0       0   2343648657963696613913171333628   
3          0       0   1144967947161920665184648209856   
4          0       0   1473699593132897455322987860217   
5          0       0   3499842459992268746782439655472   
6          0       0   6773046192039395478418961398032   
7          0       0   8337557199042282578392336267925   
8          0       0  13255259574610367856160498002633   
9          0       0  11084042807802927030360944027410   
10         0       0  10745874291280903963945800569582   
11         0       0   9234566710857371184191287327713   
12         0       0   8538575007748661072634793743666   
13         0       0   7625302915343464792568277828898   
14         0       0   6789485768664491390994883334051 

In [11]:
import requests
import pandas as pd

def get_all_tick_hour_datas(api_url, pool_address):
    # GraphQL query
    graphql_query = """
    query {
      tickHourDatas(
        where: {pool_in: ["%s"]}
        skip: %d
        first: 1000
      ) {
        id
        periodStartUnix
        pool {
          id
          token0 {
            id
            symbol
          }
          token1 {
            id
            symbol
          }
        }
        tick {
          id
        }
        liquidityGross
        liquidityNet
        volumeToken0
        volumeToken1
        volumeUSD
        feesUSD
      }
    }
    """ % (pool_address, 0)

    # Initialize variables
    all_tick_hour_datas = []
    page = 0
    limit = 1000
   # print(graphql_query)
    while True:
        # Update the skip parameter in the GraphQL query
        graphql_query = graphql_query.replace('skip: %d' % page, 'skip: %d' % (page * limit))

        # Send GraphQL request
        response = requests.post(api_url, json={'query': graphql_query})
        data = response.json().get('data', {}).get('tickHourDatas', [])

        # Append the results to the list
        all_tick_hour_datas.extend(data)

        # Break the loop if there are no more results
        if len(data) < limit:
            break

        # Increment page for the next request
        page += 1

    return all_tick_hour_datas

# Example usage
pool_address = "0xcbcdf9626bc03e24f779434178a73a0b4bad62ed"  # Replace with your pool address
api_url = "https://api.thegraph.com/subgraphs/name/uniswap/uniswap-v3"
result = get_all_tick_hour_datas(api_url, pool_address)

# Now 'result' contains all the tickHourDatas

In [19]:
import requests
import json

base_url = "https://api.tardis.dev/v1/exchanges/deribit"

def get_historical_data(symbol, instrument_type, start_timestamp, end_timestamp, interval):
    params = {
        "instrument_name": symbol + "-" + instrument_type,
        "start_timestamp": start_timestamp,
        "end_timestamp": end_timestamp,
        "interval": interval
    }

    response = requests.get(base_url + "get_tradingview_chart_data", params=params)
    data = json.loads(response.text)
    return data

# Example usage
symbol = "BTC"
instrument_type = "PERPETUAL"  # or "future"
start_timestamp = 1609459200  # Example: 01/01/2021
end_timestamp = 1640995200    # Example: 01/01/2022
interval = "1d"  # or "1h", "15m", etc.

historical_data = get_historical_data(symbol, instrument_type, start_timestamp, end_timestamp, interval)
print(historical_data)

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): www.deribit.com:443
DEBUG:urllib3.connectionpool:https://www.deribit.com:443 "GET /api/v2/public/get_tradingview_chart_data?instrument_name=BTC-PERPETUAL&start_timestamp=1609459200&end_timestamp=1640995200&interval=1d HTTP/1.1" 400 201


{'usOut': 1704280643436414, 'usIn': 1704280643436398, 'usDiff': 16, 'testnet': False, 'jsonrpc': '2.0', 'error': {'message': 'Invalid params', 'data': {'reason': 'value required', 'param': 'resolution'}, 'code': -32602}}


In [3]:
import yfinance as yf

# Get Historical Data for BTC-USD
btc = yf.Ticker("ETH-USD")
btc_hist = btc.history(start='2023-05-24', end='2023-12-26', interval="1h")

btc_hist.index = btc_hist.index.strftime("%Y-%m-%d %H:%M:%S")

# Display the modified DataFrame
#print(df)
print(btc_hist)
btc_hist.to_csv('eth_hist.csv')




                            Open         High          Low        Close  \
Datetime                                                                  
2023-05-24 00:00:00  1854.299683  1854.299683  1847.911743  1849.579956   
2023-05-24 01:00:00  1849.905151  1850.769165  1845.904907  1845.904907   
2023-05-24 02:00:00  1845.512817  1847.836914  1844.752075  1846.443115   
2023-05-24 03:00:00  1846.228149  1846.486816  1815.897095  1821.924927   
2023-05-24 04:00:00  1822.494629  1827.190063  1818.920166  1827.190063   
...                          ...          ...          ...          ...   
2023-12-25 19:00:00  2275.025391  2277.365967  2272.587402  2275.129883   
2023-12-25 20:00:00  2271.861572  2273.359619  2259.037354  2268.155273   
2023-12-25 21:00:00  2268.347900  2271.923584  2262.459961  2271.923584   
2023-12-25 22:00:00  2271.930420  2286.396973  2271.472900  2285.139893   
2023-12-25 23:00:00  2285.414307  2285.414307  2272.746826  2272.894043   

                       V